# Carregamento

In [2]:
import geopy
import numpy as np
import time
import pandas as pd
from geopy.geocoders import Nominatim
from geopy import Point

df = pd.read_csv('target_apartments1.csv')
df = df.drop_duplicates()


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
df['point'] = df.apply(lambda row: Point(latitude=row['latitude'], longitude=row['longitude']), axis=1)
geolocator = Nominatim(domain='localhost:8080', scheme='http')

def thread_wrapper_func(df):
    return df.apply(locate_neighborhood, axis=1)


def locate_neighborhood(df):
    raw_response = geolocator.reverse(df).raw
    address = raw_response.get('address', None)
    if address == None:
        return None
    neighborhood = address.get('city_district', None)
    if neighborhood is None:
        neighborhood = address.get('suburb', None)
    return neighborhood

import concurrent.futures
def parallelize_dataframe(df, func, n_threads=4):
    df_split = np.array_split(df, n_threads)
    with concurrent.futures.ThreadPoolExecutor(max_workers=n_threads) as executor:
        df = pd.concat(executor.map(func, df_split))
    return df

df['neighborhood'] = parallelize_dataframe(df[['point']], thread_wrapper_func, n_threads=16)
df.to_csv('target_apartments1_wn.csv', index=False)